In [27]:
from __future__ import print_function
import numpy as np
np.random.seed(1337)  # for reproducibility

import matplotlib
# Force matplotlib to not use any Xwindows backend.
matplotlib.use('Agg')

#from keras.datasets import mnist
from keras.models import Sequential
#from keras.layers import Dense, Dropout, Activation, Flatten
#from keras.layers import Convolution2D, MaxPooling2D
from keras.layers.core import Dense, Dropout, Activation, Flatten
from keras.layers.convolutional import Convolution2D, MaxPooling2D
from keras.utils import np_utils
from keras import backend as K
from keras.models import model_from_json


import skimage.io as io 
import matplotlib.pyplot as plt
from os import listdir
from os.path import isfile, join
import os 

In [ ]:
# https://blog.rescale.com/neural-networks-using-keras-on-rescale/
# https://gist.github.com/baraldilorenzo/07d7802847aaad0a35d3
# https://github.com/fchollet/keras/issues/1627
# http://stackoverflow.com/questions/37088571/keras-loading-color-images

In [40]:
batch_size = 32
nb_epoch = 3
# number of convolutional filters to use
nb_filters = 32
# size of pooling area for max pooling
pool_size = (2, 2)
# convolution kernel size
kernel_size = (3, 3)

In [30]:
# the data, shuffled and split between train and test sets
path_class_0 = '/archive1/ahem_data/class_0/'
path_class_1 = '/archive1/ahem_data/class_1/'

nb_classes = 2
#input_shape = (1, img_rows, img_cols)

class0_files = [f for f in listdir(path_class_0) if isfile(join(path_class_0, f))]
class1_files = [f for f in listdir(path_class_1) if isfile(join(path_class_1, f))]

In [31]:
X_t = []
Y_t = []

for fn in class0_files[:100]:
    img = io.imread(os.path.join(path_class_0, fn))
    img = img.transpose((2,0,1))
    img = img[:3, :, :]
    X_t.append(img)
    Y_t.append(0)

for fn in class1_files[:100]:
    img = io.imread(os.path.join(path_class_1, fn))
    img = img.transpose((2,0,1))
    img = img[:3, :, :]
    X_t.append(img)
    Y_t.append(1)

X_t = np.asarray(X_t)
X_t = X_t.astype('float32')
X_t /= 255

Y_t = np.asarray(Y_t)
Y_t = np_utils.to_categorical(Y_t, nb_classes)

In [52]:
X_t.shape

(152, 3, 191, 463)

In [53]:
img_rows, img_cols = X_t.shape[2], X_t.shape[3]  # this is big already 
# input image dimensions
img_channels = 3               # RGB
input_shape = (3, img_rows, img_cols)

In [20]:
## test set
X_test = []
Y_test = [] 

for fn in class0_files[6000:8000]:
    img = io.imread(os.path.join(path_class_0, fn))
    img = img.transpose((2,0,1))
    img = img[:3, :, :]
    X_test.append(img)
    Y_test.append(0)

for fn in class1_files[6000:8000]:
    img = io.imread(os.path.join(path_class_1, fn))
    img = img.transpose((2,0,1))
    img = img[:3, :, :]
    X_test.append(img)
    Y_test.append(1)

X_test = np.asarray(X_test)
Y_test = np.asarray(Y_test)
X_test = X_test.astype('float32')
X_test /= 255

Y_test = np_utils.to_categorical(Y_test, nb_classes)

In [ ]:
"""def generate_batch_data(vocPath,imageNameFile,batch_size):
    sample_number = 5000 
    class_num = 20

    while 1:

        for i in range(0,sample_number,batch_size):
            #Read a batch of images from files
            imageList = prepareBatch(i,i+batch_size,imageNameFile,vocPath)
            #process imageList to np arrays images and boxes
            yield np.asarray(images),np.asarray(boxes)
"""

In [186]:
#permutation = np.random.randint(6000,10000, 40)

In [268]:
# seems to break
#permutation = np.random.permutation(142)
#X_test = X_t[permutation]
#Y_test = Y_t[permutation]

In [109]:
""" 

def train_model(model, X_train, Y_train, X_test, Y_test):
    nb_epoch = 1
    batch_size = 16
    optimizer='adadelta' 
    
    #sgd = SGD(lr=0.01, decay=1e-6, momentum=0.9, nesterov=True)
    model.compile(loss='categorical_crossentropy', optimizer=optimizer)
 
    model.fit(X_train, Y_train, nb_epoch=nb_epoch, 
              batch_size=batch_size,
              #validation_split=0.1, 
              show_accuracy=True, 
              verbose=1)
 
    #print('Testing...')
    #res = model.evaluate(X_test, Y_test, batch_size=batch_size, verbose=1, show_accuracy=True)
    #print('Test accuracy: {0}'.format(res[1]))
    
""" 

" \n\ndef train_model(model, X_train, Y_train, X_test, Y_test):\n    nb_epoch = 1\n    batch_size = 16\n    optimizer='adadelta' \n    \n    #sgd = SGD(lr=0.01, decay=1e-6, momentum=0.9, nesterov=True)\n    model.compile(loss='categorical_crossentropy', optimizer=optimizer)\n \n    model.fit(X_train, Y_train, nb_epoch=nb_epoch, \n              batch_size=batch_size,\n              #validation_split=0.1, \n              show_accuracy=True, \n              verbose=1)\n \n    #print('Testing...')\n    #res = model.evaluate(X_test, Y_test, batch_size=batch_size, verbose=1, show_accuracy=True)\n    #print('Test accuracy: {0}'.format(res[1]))\n    \n"

In [54]:
def make_model():
    model = Sequential()

    model.add(Convolution2D(nb_filters, kernel_size[0], kernel_size[1],
                            border_mode='valid',
                            input_shape=input_shape))
    model.add(Activation('relu'))
    model.add(Convolution2D(nb_filters, kernel_size[0], kernel_size[1]))
    model.add(Activation('relu'))
    model.add(MaxPooling2D(pool_size=pool_size))
    model.add(Dropout(0.25))

    
    model.add(Convolution2D(nb_filters, 3, 3, border_mode='same'))
    model.add(Activation('relu'))
    model.add(Convolution2D(nb_filters, 3, 3))
    model.add(Activation('relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(Dropout(0.25))
    

    model.add(Flatten())
    model.add(Dense(128))
    model.add(Activation('relu'))
    model.add(Dropout(0.5))
    model.add(Dense(nb_classes))
    model.add(Activation('softmax'))


    model.compile(loss='binary_crossentropy',
                  optimizer='adadelta',
                  metrics=['accuracy'])
    return model 

In [55]:
def save_model(model):
    model_json = model.to_json()
    open('ahem_architecture.json', 'w').write(model_json)
    model.save_weights('ahem_weights.h5', overwrite=True)
    

def load_model(model_def_fname, model_weight_fname):
    model = model_from_json(open(model_def_fname).read())
    model.load_weights(model_weight_fname)
    return model

def load_image(filename):
    img = io.imread(filename)
    img = img.transpose((2,0,1))
    img = img[:3, :, :]
    return img

In [56]:
model = make_model()

In [37]:
# if load existing model, compile before fitting
#model = load_model('ahem_architecture.json', 'ahem_weights.h5')

In [57]:
model.compile(loss='binary_crossentropy', optimizer='adadelta', metrics=['accuracy'])

In [156]:
for e in xrange(3):
    model.fit(X_t, Y_t, 
              #validation_data=(X_test, Y_test), 
              batch_size=batch_size, 
              nb_epoch=1, verbose=1)
    save_model(model)

Epoch 1/1
152/152 [==============================] - 531s - loss: 0.3419 - acc: 0.8816    
Epoch 1/1
152/152 [==============================] - 531s - loss: 0.3189 - acc: 0.9013    
Epoch 1/1
152/152 [==============================] - 531s - loss: 0.4343 - acc: 0.8158    


## Trying if all this stuff works

In [47]:
predictions = model.predict_classes(X_test)

#predictions

y = []
for e in Y_test:
    if e[0]> e[1]:
        y.append(0)
    else:
        y.append(1)

print('how many did we guess out of ', Y_test.shape)
np.sum(y == predictions)  

# New audio sample 

In [60]:
import utils as ut

In [69]:
# the data, shuffled and split between train and test sets
path_newsample = '/archive1/ahem_data/new_sample/'
newsample_files = [f for f in listdir(path_newsample) if isfile(join(path_newsample, f))]

In [70]:
X_test = []

for fn in newsample_files:
    img = io.imread(os.path.join(path_newsample, fn))
    img = img.transpose((2,0,1))
    img = img[:3, :, :]
    X_test.append(img)

X_test = np.asarray(X_test)
X_test = X_test.astype('float32')
X_test /= 255

In [157]:
X_test.shape

(394, 3, 191, 463)

In [158]:
predictions = model.predict_classes(X_test)

394/394 [==============================] - 407s    


In [159]:
# index of prediction =1 are noisy
noisy_frames = np.where(predictions==1)[0]

In [161]:
noisy_files = [newsample_files[n] for n in noisy_frames] 
noisy_files

['partial_spectrum_384000.png',
 'partial_spectrum_390000.png',
 'partial_spectrum_663000.png',
 'partial_spectrum_675000.png',
 'partial_spectrum_669000.png',
 'partial_spectrum_684000.png',
 'partial_spectrum_660000.png',
 'partial_spectrum_198000.png',
 'partial_spectrum_1074000.png',
 'partial_spectrum_666000.png',
 'partial_spectrum_210000.png',
 'partial_spectrum_1173000.png',
 'partial_spectrum_426000.png',
 'partial_spectrum_207000.png',
 'partial_spectrum_204000.png',
 'partial_spectrum_27000.png',
 'partial_spectrum_480000.png',
 'partial_spectrum_195000.png',
 'partial_spectrum_477000.png',
 'partial_spectrum_468000.png',
 'partial_spectrum_672000.png',
 'partial_spectrum_732000.png',
 'partial_spectrum_1005000.png',
 'partial_spectrum_381000.png',
 'partial_spectrum_471000.png',
 'partial_spectrum_387000.png',
 'partial_spectrum_459000.png',
 'partial_spectrum_474000.png',
 'partial_spectrum_678000.png',
 'partial_spectrum_201000.png',
 'partial_spectrum_462000.png',
 'part

In [59]:
ut.plot_waves(sound_names,raw_sounds)

In [61]:
ut.plot_specgram(list(sound_names[3:]), list(raw_sounds[3:]))

In [62]:
ut.plot_log_power_specgram(sound_names,raw_sounds)

In [63]:
plt.show()

In [8]:
 mfccs, chroma, mel, contrast,tonnetz = extract_feature('./data/jingle.wav')

/usr/local/lib/python2.7/dist-packages/numpy/core/numeric.py:482: VisibleDeprecationWarning: using a non-integer number instead of an integer will result in an error in the future
  return array(a, dtype, copy=False, order=order)


In [10]:
mfccs.shape

(40,)

In [12]:
chroma.shape

(12,)

In [14]:
mel.shape

(128,)

In [16]:
contrast.shape

(7,)

In [18]:
tonnetz.shape

(6,)

In [69]:
ut.specgram_frombuffer(raw_sounds[2][0:44100], 6, 6, fname='/archive1/buffer.png', show=True)

## Playback and clean new samples

In [162]:
import librosa
import librosa.display
import IPython.display
import numpy as np

import numpy as np
from skimage.measure import block_reduce
import skimage.io as io 

import matplotlib.pyplot as plt
import matplotlib.image as mpimg
import matplotlib.style as ms
ms.use('seaborn-muted')
%matplotlib inline

In [179]:
# Load the example track
path = '/archive1/ahem_data'
sound_file_paths = [os.path.join(path, "provocation_dirty.wav")]
sound_names = ["dirty"]
raw_sounds = ut.load_sound_files(sound_file_paths)
windowsize = 6000 

# create positive samples
audiosamples = raw_sounds[0]
numsamples = audiosamples.shape[0]

In [180]:
original_audio = audiosamples
clean_audio = audiosamples

In [194]:
# Play it back!
IPython.display.Audio(data=original_audio, rate=44100)

In [195]:
import librosa


In [197]:
librosa.output.write_wav('/archive1/ahem_data/cleaned.wav', original_audio, sr=44100)

In [182]:
noisy_start = []
for fn in noisy_files:
    noisy_start.append(int(fn.split('_')[2].split('.')[0]))

In [183]:
noisy_start.sort(reverse=True)

In [184]:
len(noisy_start)

32

In [185]:
clean_audio = audiosamples
prev_idx = 0
for start in xrange(1, len(noisy_start)):
    prev_pos  = noisy_start[prev_idx]
    current_pos = noisy_start[start]
    diff = prev_pos - current_pos
    prev_idx += 1

    #print(prev_pos, current_pos, diff)
    #if diff>3000:
    clean_audio[current_pos:current_pos+windowsize] = 0

In [188]:
# Play it back!
IPython.display.Audio(data=clean_audio, rate=44100)

In [191]:
tmp = np.zeros((144, 1, 265, 197), dtype=np.bool)

In [192]:
tmp.shape

(144, 1, 265, 197)